In [ ]:
import torch
import torchvision
import numpy as np
import logging
logging.basicConfig(level=logging.INFO, format="%(asctime)s %(name)-12s %(levelname)-8s %(message)s")

from benchmark import ImageBenchmark
bench = ImageBenchmark()
models = list(bench.list_models())
models_dict = {}
for i, model in enumerate(models):
    if not model.torch_model_exists():
        continue
    print(f'{i}\t {model.__str__()}')
    models_dict[model.__str__()] = model

In [ ]:
from modeldiff import ModelDiff

def compare_with_seed(model1, model2, truth=-1):
    print(f'comparing:\n  model1={model1}\n  model2={model2}')
    md = ModelDiff(model1, model2)
    seed_inputs = md.get_seed_inputs(rand=False)
    sim = md.compute_similarity_with_inputs(seed_inputs)
    if truth == -1:
        truth = 1 if model1.__str__().split('-')[0] == model2.__str__().split('-')[0] else 0
    print(f' similarity is {sim}, truth is {truth}')

def test(compare):
    compare(models[23], models[38], 1) # should be similar
    compare(models[1], models[0], 0)   # should be different
    compare(models[13], models[25], 0) # should be different
    compare(models[13], models[22], 0) # should be different
    compare(models[1], models[17], 1)  # should be similar
    compare(models[16], models[13], 1) # should be similar
    compare(models[13], models[12], 1) # should be similar
    
# test(compare_with_seed)

In [ ]:
DEVICE = 'cuda'

def gen_adv_inputs(model, inputs):
    from advertorch.attacks import LinfPGDAttack
    def myloss(yhat, y):
        return -((yhat[:,0]-y[:,0])**2 + 0.1*((yhat[:,1:]-y[:,1:])**2).mean(1)).mean()
        
    model = model.to(DEVICE)
    inputs = torch.from_numpy(inputs).to(DEVICE)
    with torch.no_grad():
        model.eval()
        clean_outputs = model(inputs)
    
    output_shape = clean_outputs.shape
    batch_size = output_shape[0]
    num_classes = output_shape[1]
    
    y = torch.zeros(size=output_shape).to(DEVICE)
    y[:, 0] = 1000
    # more diversity
#     rand_idx = torch.randint(low=0, high=num_classes, size=(batch_size,))
#     y = torch.nn.functional.one_hot(rand_idx, num_classes=num_classes).to(DEVICE) * 10
#     print(y)
    
    adversary = LinfPGDAttack(
        model, loss_fn=myloss, eps=0.1,
        nb_iter=40, eps_iter=0.01, 
        rand_init=True, clip_min=-2.2, clip_max=2.2,
        targeted=False
    )
    
    adv_inputs = adversary.perturb(inputs, y)
    
    with torch.no_grad():
        model.eval()
        adv_outputs = model(adv_inputs).to('cpu').numpy()
#     print(adv_outputs)
    torch.cuda.empty_cache()
    return adv_inputs.to('cpu').numpy()


model = models_dict['pretrain(mbnetv2,ImageNet)-transfer(Flower102,0.1)-prune(0.2)-']
seed_inputs = model.get_seed_inputs(100, rand=False)
seed_outputs = model.batch_forward(seed_inputs)
_, seed_preds = seed_outputs.to('cpu').data.max(1)

adv_inputs = gen_adv_inputs(model.torch_model, seed_inputs)
adv_outputs = model.batch_forward(adv_inputs)
_, adv_preds = adv_outputs.to('cpu').data.max(1)

print(f"seed_preds={seed_preds}, adv_preds={adv_preds}")

In [29]:
DEVICE = 'cuda'
image_size = 224

def expand_vector(x, size):
    batch_size = x.size(0)
    x = x.view(-1, 3, size, size)
    z = torch.zeros(batch_size, 3, image_size, image_size).to(DEVICE)
    z[:, :, :size, :size] = x
    return z

def normalize(x):
    return utils.apply_normalization(x, 'imagenet')

def get_probs(model, x, y):
    output = model(x)
    probs = torch.index_select(torch.nn.functional.softmax(output, -1).data, 1, y)
    return torch.diag(probs).cpu()

def get_preds(model, x):
    output = model(x)
    _, preds = output.data.max(1)
    return preds

# runs simba on a batch of images <images_batch> with true labels (for untargeted attack) or target labels
# (for targeted attack) <labels_batch>
def dct_attack_batch(model, images_batch, labels_batch, max_iters, freq_dims, stride, epsilon, order='rand', targeted=False, pixel_attack=False, log_every=1):
    batch_size = images_batch.size(0)
    image_size = images_batch.size(2)
    # sample a random ordering for coordinates independently per batch element
    if order == 'rand':
        indices = torch.randperm(3 * freq_dims * freq_dims)[:max_iters]
    elif order == 'diag':
        indices = utils.diagonal_order(image_size, 3)[:max_iters]
    elif order == 'strided':
        indices = utils.block_order(image_size, 3, initial_size=freq_dims, stride=stride)[:max_iters]
    else:
        indices = utils.block_order(image_size, 3)[:max_iters]
    if order == 'rand':
        expand_dims = freq_dims
    else:
        expand_dims = image_size
    n_dims = 3 * expand_dims * expand_dims
    x = torch.zeros(batch_size, n_dims)
    # logging tensors
    probs = torch.zeros(batch_size, max_iters)
    succs = torch.zeros(batch_size, max_iters)
    queries = torch.zeros(batch_size, max_iters)
    l2_norms = torch.zeros(batch_size, max_iters)
    linf_norms = torch.zeros(batch_size, max_iters)
    prev_probs = get_probs(model, images_batch, labels_batch)
    preds = get_preds(model, images_batch)
    if pixel_attack:
        trans = lambda z: z
    else:
        trans = lambda z: utils.block_idct(z, block_size=image_size, linf_bound=args.linf_bound)
    remaining_indices = torch.arange(0, batch_size).long()
    for k in range(max_iters):
        dim = indices[k]
        expanded = (images_batch[remaining_indices] + trans(expand_vector(x[remaining_indices], expand_dims))).clamp(0, 1)
        perturbation = trans(expand_vector(x, expand_dims))
        l2_norms[:, k] = perturbation.view(batch_size, -1).norm(2, 1)
        linf_norms[:, k] = perturbation.view(batch_size, -1).abs().max(1)[0]
        preds_next = get_preds(model, expanded)
        preds[remaining_indices] = preds_next
        if targeted:
            remaining = preds.ne(labels_batch)
        else:
            remaining = preds.eq(labels_batch)
        # check if all images are misclassified and stop early
        if remaining.sum() == 0:
            adv = (images_batch + trans(expand_vector(x, expand_dims))).clamp(0, 1)
            probs_k = get_probs(model, adv, labels_batch)
            probs[:, k:] = probs_k.unsqueeze(1).repeat(1, max_iters - k)
            succs[:, k:] = torch.ones(batch_size, max_iters - k)
            queries[:, k:] = torch.zeros(batch_size, max_iters - k)
            break
        remaining_indices = torch.arange(0, batch_size)[remaining].long()
        if k > 0:
            succs[:, k-1] = ~remaining
        diff = torch.zeros(remaining.sum(), n_dims)
        diff[:, dim] = epsilon
        left_vec = x[remaining_indices] - diff
        right_vec = x[remaining_indices] + diff
        # trying negative direction
        adv = (images_batch[remaining_indices] + trans(expand_vector(left_vec, expand_dims))).clamp(0, 1)
        left_probs = get_probs(model, adv, labels_batch[remaining_indices])
        queries_k = torch.zeros(batch_size)
        # increase query count for all images
        queries_k[remaining_indices] += 1
        if targeted:
            improved = left_probs.gt(prev_probs[remaining_indices])
        else:
            improved = left_probs.lt(prev_probs[remaining_indices])
        # only increase query count further by 1 for images that did not improve in adversarial loss
        if improved.sum() < remaining_indices.size(0):
            queries_k[remaining_indices[~improved]] += 1
        # try positive directions
        adv = (images_batch[remaining_indices] + trans(expand_vector(right_vec, expand_dims))).clamp(0, 1)
        right_probs = get_probs(model, adv, labels_batch[remaining_indices])
        if targeted:
            right_improved = right_probs.gt(torch.max(prev_probs[remaining_indices], left_probs))
        else:
            right_improved = right_probs.lt(torch.min(prev_probs[remaining_indices], left_probs))
        probs_k = prev_probs.clone()
        # update x depending on which direction improved
        if improved.sum() > 0:
            left_indices = remaining_indices[improved]
            left_mask_remaining = improved.unsqueeze(1).repeat(1, n_dims)
            x[left_indices] = left_vec[left_mask_remaining].view(-1, n_dims)
            probs_k[left_indices] = left_probs[improved]
        if right_improved.sum() > 0:
            right_indices = remaining_indices[right_improved]
            right_mask_remaining = right_improved.unsqueeze(1).repeat(1, n_dims)
            x[right_indices] = right_vec[right_mask_remaining].view(-1, n_dims)
            probs_k[right_indices] = right_probs[right_improved]
        probs[:, k] = probs_k
        queries[:, k] = queries_k
        prev_probs = probs[:, k]
        if (k + 1) % log_every == 0 or k == max_iters - 1:
            print('Iteration %d: queries = %.4f, prob = %.4f, remaining = %.4f' % (
                    k + 1, queries.sum(1).mean(), probs[:, k].mean(), remaining.float().mean()))
    expanded = (images_batch + trans(expand_vector(x, expand_dims))).clamp(0, 1)
    preds = get_preds(model, expanded)
    if targeted:
        remaining = preds.ne(labels_batch)
    else:
        remaining = preds.eq(labels_batch)
    succs[:, max_iters-1] = ~remaining
    return expanded, probs, succs, queries, l2_norms, linf_norms


def search_adv_inputs(model, inputs, labels):
    images_batch = torch.from_numpy(inputs).to(DEVICE)
#     labels_batch = torch.zeros(len(inputs)).long().to(DEVICE)
    labels_batch = labels.long().to(DEVICE)
    with torch.no_grad():
        adv, probs, succs, queries, l2_norms, linf_norms = dct_attack_batch(
            model, images_batch=images_batch, labels_batch=labels_batch,
            max_iters=5000, freq_dims=image_size, stride=7, epsilon=0.2, order='rand',
            targeted=False, pixel_attack=True, log_every=10
        )
    return adv


model = models_dict['pretrain(mbnetv2,ImageNet)-transfer(Flower102,0.1)-prune(0.2)-']
seed_inputs = model.get_seed_inputs(100, rand=False)
seed_outputs = model.batch_forward(seed_inputs)
_, seed_preds = seed_outputs.to('cpu').data.max(1)

adv_inputs = search_adv_inputs(model.torch_model, seed_inputs, seed_preds)
adv_outputs = model.batch_forward(adv_inputs)
_, adv_preds = adv_outputs.to('cpu').data.max(1)

print(f"seed_preds={seed_preds}, adv_preds={adv_preds}")


Iteration 10: queries = 8.6000, prob = 0.7065, remaining = 0.4900
Iteration 20: queries = 17.8100, prob = 0.7058, remaining = 0.4900
Iteration 30: queries = 26.9500, prob = 0.7050, remaining = 0.4900
Iteration 40: queries = 36.2300, prob = 0.7045, remaining = 0.4900
Iteration 50: queries = 45.3600, prob = 0.7039, remaining = 0.4900
Iteration 60: queries = 54.4400, prob = 0.7034, remaining = 0.4900
Iteration 70: queries = 63.4700, prob = 0.7028, remaining = 0.4800
Iteration 80: queries = 72.2800, prob = 0.7022, remaining = 0.4800
Iteration 90: queries = 81.2800, prob = 0.7017, remaining = 0.4800
Iteration 100: queries = 90.1300, prob = 0.7010, remaining = 0.4800
Iteration 110: queries = 99.1700, prob = 0.7007, remaining = 0.4800
Iteration 120: queries = 108.0500, prob = 0.7002, remaining = 0.4800
Iteration 130: queries = 116.8700, prob = 0.6994, remaining = 0.4800
Iteration 140: queries = 125.7600, prob = 0.6989, remaining = 0.4800
Iteration 150: queries = 134.8000, prob = 0.6984, remai

Iteration 1200: queries = 959.2500, prob = 0.6520, remaining = 0.3800
Iteration 1210: queries = 966.4300, prob = 0.6517, remaining = 0.3700
Iteration 1220: queries = 973.1700, prob = 0.6514, remaining = 0.3500
Iteration 1230: queries = 979.8200, prob = 0.6511, remaining = 0.3500
Iteration 1240: queries = 986.5000, prob = 0.6508, remaining = 0.3500
Iteration 1250: queries = 993.0600, prob = 0.6506, remaining = 0.3500
Iteration 1260: queries = 999.6900, prob = 0.6503, remaining = 0.3500
Iteration 1270: queries = 1006.2600, prob = 0.6501, remaining = 0.3500
Iteration 1280: queries = 1012.7600, prob = 0.6496, remaining = 0.3500
Iteration 1290: queries = 1019.2800, prob = 0.6494, remaining = 0.3500
Iteration 1300: queries = 1025.8400, prob = 0.6490, remaining = 0.3500
Iteration 1310: queries = 1032.4700, prob = 0.6487, remaining = 0.3400
Iteration 1320: queries = 1038.8700, prob = 0.6483, remaining = 0.3400
Iteration 1330: queries = 1045.1500, prob = 0.6479, remaining = 0.3400
Iteration 134

Iteration 2360: queries = 1635.6200, prob = 0.6199, remaining = 0.2900
Iteration 2370: queries = 1641.1100, prob = 0.6196, remaining = 0.2900
Iteration 2380: queries = 1646.5400, prob = 0.6194, remaining = 0.2900
Iteration 2390: queries = 1651.9100, prob = 0.6192, remaining = 0.2900
Iteration 2400: queries = 1657.3400, prob = 0.6190, remaining = 0.2900
Iteration 2410: queries = 1662.8000, prob = 0.6188, remaining = 0.2900
Iteration 2420: queries = 1668.2500, prob = 0.6186, remaining = 0.2900
Iteration 2430: queries = 1673.8199, prob = 0.6184, remaining = 0.2900
Iteration 2440: queries = 1679.1899, prob = 0.6181, remaining = 0.2900
Iteration 2450: queries = 1684.6400, prob = 0.6179, remaining = 0.2900
Iteration 2460: queries = 1690.0400, prob = 0.6177, remaining = 0.2900
Iteration 2470: queries = 1695.3700, prob = 0.6173, remaining = 0.2900
Iteration 2480: queries = 1700.6600, prob = 0.6169, remaining = 0.2800
Iteration 2490: queries = 1705.9900, prob = 0.6167, remaining = 0.2800
Iterat

Iteration 3520: queries = 2169.8501, prob = 0.5989, remaining = 0.2100
Iteration 3530: queries = 2173.7500, prob = 0.5987, remaining = 0.2100
Iteration 3540: queries = 2177.6499, prob = 0.5986, remaining = 0.2100
Iteration 3550: queries = 2181.6001, prob = 0.5984, remaining = 0.2100
Iteration 3560: queries = 2185.5300, prob = 0.5983, remaining = 0.2100
Iteration 3570: queries = 2189.4299, prob = 0.5982, remaining = 0.2100
Iteration 3580: queries = 2193.4199, prob = 0.5980, remaining = 0.2100
Iteration 3590: queries = 2197.4099, prob = 0.5979, remaining = 0.2100
Iteration 3600: queries = 2201.3301, prob = 0.5978, remaining = 0.2100
Iteration 3610: queries = 2205.2800, prob = 0.5977, remaining = 0.2100
Iteration 3620: queries = 2209.2500, prob = 0.5976, remaining = 0.2100
Iteration 3630: queries = 2213.0601, prob = 0.5974, remaining = 0.2100
Iteration 3640: queries = 2217.0100, prob = 0.5972, remaining = 0.2100
Iteration 3650: queries = 2220.9500, prob = 0.5971, remaining = 0.2100
Iterat

Iteration 4680: queries = 2555.7300, prob = 0.5868, remaining = 0.1600
Iteration 4690: queries = 2558.7700, prob = 0.5867, remaining = 0.1600
Iteration 4700: queries = 2561.7900, prob = 0.5866, remaining = 0.1600
Iteration 4710: queries = 2564.5200, prob = 0.5865, remaining = 0.1500
Iteration 4720: queries = 2567.3501, prob = 0.5864, remaining = 0.1500
Iteration 4730: queries = 2570.2100, prob = 0.5864, remaining = 0.1500
Iteration 4740: queries = 2573.0200, prob = 0.5863, remaining = 0.1500
Iteration 4750: queries = 2575.8601, prob = 0.5861, remaining = 0.1500
Iteration 4760: queries = 2578.6299, prob = 0.5861, remaining = 0.1400
Iteration 4770: queries = 2581.3101, prob = 0.5860, remaining = 0.1400
Iteration 4780: queries = 2583.9500, prob = 0.5859, remaining = 0.1400
Iteration 4790: queries = 2586.6001, prob = 0.5858, remaining = 0.1400
Iteration 4800: queries = 2589.2100, prob = 0.5857, remaining = 0.1400
Iteration 4810: queries = 2591.8799, prob = 0.5856, remaining = 0.1400
Iterat

In [57]:
import torch
import torchvision
import numpy as np
import logging
logging.basicConfig(level=logging.INFO, format="%(asctime)s %(name)-12s %(levelname)-8s %(message)s")

from benchmark import ImageBenchmark
bench = ImageBenchmark()
models = list(bench.list_models())
models_dict = {}
for i, model in enumerate(models):
    if not model.torch_model_exists():
        continue
#     print(f'{i}\t {model.__str__()}')
    models_dict[model.__str__()] = model


DEVICE = 'cuda'
image_size = 224

def expand_vector(x, image_size):
    batch_size = x.size(0)
    x = x.view(-1, 3, image_size, image_size)
    z = torch.zeros(batch_size, 3, image_size, image_size).to(DEVICE)
    z[:, :, :image_size, :image_size] = x
    return z

def evaluate_inputs(model, inputs, seed_outputs, seed_preds):
    outputs = model(inputs)
    _, preds = outputs.data.max(1)
    outputs = torch.nn.functional.softmax(outputs, -1)
    seed_outputs = torch.nn.functional.softmax(seed_outputs, -1)
    reduce_dims = tuple(range(outputs.dim())[1:])
    divergence_arr = torch.sum((outputs - seed_outputs) ** 2, dim=reduce_dims) ** 0.5
    divergence = torch.mean(divergence_arr)
    diversity_matrix = torch.cdist(outputs, outputs, p=2.0)
    diversity = torch.mean(diversity_matrix)
    quantile = lambda t, q: t.view(-1).kthvalue(1 + round(float(q) * (t.numel() - 1))).values.item()
    diversity_quantile = quantile(diversity_matrix, 0.011)
#     diversity = diversity ** 2
    score = divergence + 0.5 * diversity
    succ = preds.ne(seed_preds)
    low_divergence_indices = list(torch.nonzero(divergence_arr.lt(divergence)).cpu().numpy())
    low_diversity_indices = list(torch.nonzero(diversity_matrix.lt(diversity_quantile)).cpu().numpy())
    remaining_indices = set()
    for i in low_divergence_indices:
        remaining_indices.add(i[0])
    for i in low_diversity_indices:
        if i[0] == i[1]:
            continue
        remaining_indices.add(i[0])
        remaining_indices.add(i[1])
    remaining_indices = sorted(remaining_indices)
#     print(f' low_divergence_indices={len(low_divergence_indices)}\n low_diversity_indices={len(low_diversity_indices)}\n remaining_indices={len(remaining_indices)}')
    eval_line = f'score={score:.4f}, divergence={divergence:.4f}, diversity={diversity:.4f}, num_succ={succ.sum()}'
    return {
        'outputs': outputs,
        'preds': preds,
        'score': score,
        'divergence': divergence,
        'diversity': diversity,
        'succ': succ,
        'remaining': remaining_indices,
        'eval_line': eval_line
    }
    
    
def optimize_towards_goal(model, seed_inputs, seed_outputs, seed_preds, max_iters=100000, epsilon=0.5, log_every=1):
#     seed_inputs = torch.from_numpy(seed_inputs).to(DEVICE)
#     seed_outputs = torch.from_numpy(seed_outputs).to(DEVICE)
#     seed_preds = torch.from_numpy(seed_preds).to(DEVICE)
    input_shape = seed_inputs[0].shape
    n_inputs = seed_inputs.shape[0]
    ndims = np.prod(input_shape)

    with torch.no_grad():
        inputs = seed_inputs
        evaluation = evaluate_inputs(model, inputs, seed_outputs, seed_preds)
        print(f'initial_evaluation: {evaluation["eval_line"]}')

        for i in range(max_iters):
#             print(f'mutation {i}-th iteration')

            mutation_pos = np.random.randint(0, ndims)
            mutation = np.zeros(ndims).astype(np.float32)
            mutation[mutation_pos] = epsilon
            mutation = np.reshape(mutation, input_shape)

            mutation_batch = np.zeros(shape=inputs.shape).astype(np.float32)
#             all_indices = list(range(0, n_inputs))
#             mutation_indices = np.random.choice(all_indices, size=int(n_inputs * 0.85), replace=False)
#             print(mutation_indices)
#             mutation_idx = np.random.randint(0, n_inputs)
            mutation_indices = evaluation['remaining']
            mutation_batch[mutation_indices] = mutation
            mutation_batch = torch.from_numpy(mutation_batch).to(DEVICE)

            prev_score = evaluation["score"]
            mutate_right_inputs = (inputs + mutation_batch).clamp(0, 1)
            mutate_right_eval = evaluate_inputs(model, mutate_right_inputs, seed_outputs, seed_preds)
            mutate_right_score = mutate_right_eval['score']
            mutate_left_inputs = (inputs - mutation_batch).clamp(0, 1)
            mutate_left_eval = evaluate_inputs(model, mutate_left_inputs, seed_outputs, seed_preds)
            mutate_left_score = mutate_left_eval['score']

            if mutate_right_score <= prev_score and mutate_left_score <= prev_score:
                continue
            if mutate_right_score > mutate_left_score:
#                 print(f'mutate right: {prev_score}->{mutate_right_score}')
                inputs = mutate_right_inputs
                evaluation = mutate_right_eval
            else:
#                 print(f'mutate left: {prev_score}->{mutate_left_score}')
                inputs = mutate_left_inputs
                evaluation = mutate_left_eval
#             if i+1 % log_every == 0:
            print(f'{i:4d}-th evaluation: {evaluation["eval_line"]}')
        return inputs

model = models_dict['pretrain(mbnetv2,ImageNet)-transfer(Flower102,0.1)-prune(0.2)-']
seed_inputs = model.get_seed_inputs(100, rand=False)
seed_inputs = torch.from_numpy(seed_inputs).to(DEVICE)
seed_outputs = model.batch_forward(seed_inputs)
_, seed_preds = seed_outputs.data.max(1)

adv_inputs = optimize_towards_goal(model.torch_model_on_device, seed_inputs, seed_outputs, seed_preds)
adv_outputs = model.batch_forward(adv_inputs).cpu()
_, adv_preds = adv_outputs.data.max(1)

print(f"seed_preds={seed_preds}, adv_preds={adv_preds}")

initial_evaluation: score=0.6701, divergence=0.0000, diversity=1.3403, num_succ=0
   0-th evaluation: score=1.0386, divergence=0.7438, diversity=0.5896, num_succ=56
   1-th evaluation: score=1.0387, divergence=0.7439, diversity=0.5895, num_succ=56
   2-th evaluation: score=1.0388, divergence=0.7439, diversity=0.5897, num_succ=56
   3-th evaluation: score=1.0388, divergence=0.7439, diversity=0.5897, num_succ=56
   4-th evaluation: score=1.0391, divergence=0.7442, diversity=0.5897, num_succ=56
   5-th evaluation: score=1.0391, divergence=0.7443, diversity=0.5898, num_succ=56
   6-th evaluation: score=1.0393, divergence=0.7445, diversity=0.5897, num_succ=56
   8-th evaluation: score=1.0405, divergence=0.7453, diversity=0.5903, num_succ=56
   9-th evaluation: score=1.0405, divergence=0.7453, diversity=0.5903, num_succ=56
  11-th evaluation: score=1.0405, divergence=0.7455, diversity=0.5899, num_succ=56
  12-th evaluation: score=1.0405, divergence=0.7456, diversity=0.5899, num_succ=56
  13-

 158-th evaluation: score=1.0484, divergence=0.7525, diversity=0.5918, num_succ=57
 162-th evaluation: score=1.0484, divergence=0.7525, diversity=0.5918, num_succ=57
 163-th evaluation: score=1.0484, divergence=0.7525, diversity=0.5917, num_succ=57
 164-th evaluation: score=1.0484, divergence=0.7526, diversity=0.5917, num_succ=57
 167-th evaluation: score=1.0484, divergence=0.7526, diversity=0.5917, num_succ=57
 168-th evaluation: score=1.0486, divergence=0.7528, diversity=0.5915, num_succ=57
 169-th evaluation: score=1.0486, divergence=0.7528, diversity=0.5915, num_succ=57
 171-th evaluation: score=1.0487, divergence=0.7530, diversity=0.5914, num_succ=57
 172-th evaluation: score=1.0487, divergence=0.7530, diversity=0.5914, num_succ=57
 173-th evaluation: score=1.0487, divergence=0.7530, diversity=0.5914, num_succ=57
 174-th evaluation: score=1.0487, divergence=0.7532, diversity=0.5911, num_succ=57
 176-th evaluation: score=1.0488, divergence=0.7532, diversity=0.5911, num_succ=57
 177

 324-th evaluation: score=1.0534, divergence=0.7608, diversity=0.5852, num_succ=59
 325-th evaluation: score=1.0534, divergence=0.7609, diversity=0.5851, num_succ=59
 329-th evaluation: score=1.0534, divergence=0.7609, diversity=0.5851, num_succ=59
 330-th evaluation: score=1.0535, divergence=0.7609, diversity=0.5850, num_succ=59
 331-th evaluation: score=1.0535, divergence=0.7609, diversity=0.5850, num_succ=59
 332-th evaluation: score=1.0535, divergence=0.7609, diversity=0.5851, num_succ=59
 333-th evaluation: score=1.0535, divergence=0.7610, diversity=0.5851, num_succ=59
 335-th evaluation: score=1.0536, divergence=0.7612, diversity=0.5848, num_succ=59
 336-th evaluation: score=1.0536, divergence=0.7613, diversity=0.5847, num_succ=59
 341-th evaluation: score=1.0536, divergence=0.7613, diversity=0.5847, num_succ=59
 345-th evaluation: score=1.0536, divergence=0.7613, diversity=0.5848, num_succ=59
 347-th evaluation: score=1.0536, divergence=0.7613, diversity=0.5847, num_succ=59
 348

 494-th evaluation: score=1.0569, divergence=0.7676, diversity=0.5786, num_succ=59
 495-th evaluation: score=1.0569, divergence=0.7676, diversity=0.5786, num_succ=59
 500-th evaluation: score=1.0569, divergence=0.7676, diversity=0.5785, num_succ=59
 501-th evaluation: score=1.0569, divergence=0.7677, diversity=0.5784, num_succ=59
 502-th evaluation: score=1.0569, divergence=0.7677, diversity=0.5784, num_succ=59
 503-th evaluation: score=1.0569, divergence=0.7678, diversity=0.5783, num_succ=59
 507-th evaluation: score=1.0570, divergence=0.7678, diversity=0.5783, num_succ=59
 510-th evaluation: score=1.0570, divergence=0.7679, diversity=0.5782, num_succ=59
 513-th evaluation: score=1.0570, divergence=0.7680, diversity=0.5781, num_succ=59
 514-th evaluation: score=1.0570, divergence=0.7679, diversity=0.5782, num_succ=59
 515-th evaluation: score=1.0571, divergence=0.7680, diversity=0.5782, num_succ=59
 517-th evaluation: score=1.0571, divergence=0.7681, diversity=0.5781, num_succ=59
 518

 672-th evaluation: score=1.0606, divergence=0.7746, diversity=0.5720, num_succ=60
 676-th evaluation: score=1.0606, divergence=0.7746, diversity=0.5719, num_succ=60
 677-th evaluation: score=1.0608, divergence=0.7748, diversity=0.5719, num_succ=60
 681-th evaluation: score=1.0608, divergence=0.7749, diversity=0.5718, num_succ=60
 682-th evaluation: score=1.0608, divergence=0.7750, diversity=0.5717, num_succ=60
 683-th evaluation: score=1.0608, divergence=0.7750, diversity=0.5717, num_succ=60
 684-th evaluation: score=1.0608, divergence=0.7750, diversity=0.5717, num_succ=60
 686-th evaluation: score=1.0608, divergence=0.7752, diversity=0.5712, num_succ=60
 690-th evaluation: score=1.0609, divergence=0.7754, diversity=0.5710, num_succ=60
 692-th evaluation: score=1.0610, divergence=0.7756, diversity=0.5707, num_succ=60
 693-th evaluation: score=1.0610, divergence=0.7757, diversity=0.5707, num_succ=60
 696-th evaluation: score=1.0611, divergence=0.7757, diversity=0.5708, num_succ=60
 697

...

98994-th evaluation: score=1.7585, divergence=1.2420, diversity=1.0330, num_succ=100
98995-th evaluation: score=1.7585, divergence=1.2420, diversity=1.0330, num_succ=100
98996-th evaluation: score=1.7585, divergence=1.2420, diversity=1.0330, num_succ=100
98997-th evaluation: score=1.7585, divergence=1.2420, diversity=1.0330, num_succ=100
98999-th evaluation: score=1.7585, divergence=1.2420, diversity=1.0331, num_succ=100
99001-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99002-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99005-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99006-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99007-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99009-th evaluation: score=1.7586, divergence=1.2420, diversity=1.0331, num_succ=100
99010-th evaluation: score=1.7586, divergence=1.2420, diversity=1

99182-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99183-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99184-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99185-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99186-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99188-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99189-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99190-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99194-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99195-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99196-th evaluation: score=1.7597, divergence=1.2426, diversity=1.0342, num_succ=100
99199-th evaluation: score=1.7597, divergence=1.2426, diversity=1

99373-th evaluation: score=1.7602, divergence=1.2429, diversity=1.0347, num_succ=100
99376-th evaluation: score=1.7602, divergence=1.2429, diversity=1.0347, num_succ=100
99377-th evaluation: score=1.7602, divergence=1.2429, diversity=1.0347, num_succ=100
99378-th evaluation: score=1.7602, divergence=1.2429, diversity=1.0347, num_succ=100
99381-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0347, num_succ=100
99383-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0347, num_succ=100
99386-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0348, num_succ=100
99387-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0348, num_succ=100
99388-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0348, num_succ=100
99389-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0348, num_succ=100
99390-th evaluation: score=1.7603, divergence=1.2429, diversity=1.0348, num_succ=100
99392-th evaluation: score=1.7603, divergence=1.2429, diversity=1

99565-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0351, num_succ=100
99566-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0351, num_succ=100
99567-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0351, num_succ=100
99568-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0351, num_succ=100
99570-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0351, num_succ=100
99573-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0352, num_succ=100
99576-th evaluation: score=1.7607, divergence=1.2431, diversity=1.0352, num_succ=100
99577-th evaluation: score=1.7607, divergence=1.2432, diversity=1.0352, num_succ=100
99578-th evaluation: score=1.7607, divergence=1.2432, diversity=1.0352, num_succ=100
99579-th evaluation: score=1.7608, divergence=1.2432, diversity=1.0352, num_succ=100
99582-th evaluation: score=1.7608, divergence=1.2432, diversity=1.0352, num_succ=100
99584-th evaluation: score=1.7608, divergence=1.2432, diversity=1

99805-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99806-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99808-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99812-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99813-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99815-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99817-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99818-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99820-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99822-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99823-th evaluation: score=1.7614, divergence=1.2435, diversity=1.0358, num_succ=100
99825-th evaluation: score=1.7614, divergence=1.2435, diversity=1

In [ ]:
DEVICE = 'cuda'
import logging
logging.basicConfig(level=logging.INFO, format="%(asctime)s %(name)-12s %(levelname)-8s %(message)s")


def gen_adv_inputs(model, inputs):
    from advertorch.attacks import LinfPGDAttack
    def myloss(yhat, y):
        return -((yhat[:,0]-y[:,0])**2 + 0.1*((yhat[:,1:]-y[:,1:])**2).mean(1)).mean()
        
    model = model.to(DEVICE)
    inputs = torch.from_numpy(inputs).to(DEVICE)
    with torch.no_grad():
        model.eval()
        clean_outputs = model(inputs)
    
    output_shape = clean_outputs.shape
    batch_size = output_shape[0]
    num_classes = output_shape[1]
    
    y = torch.zeros(size=output_shape).to(DEVICE)
    y[:, 0] = 1000
    # more diversity
#     rand_idx = torch.randint(low=0, high=num_classes, size=(batch_size,))
#     y = torch.nn.functional.one_hot(rand_idx, num_classes=num_classes).to(DEVICE) * 10
#     print(y)
    
    adversary = LinfPGDAttack(
        model, loss_fn=myloss, eps=0.1,
        nb_iter=40, eps_iter=0.01, 
        rand_init=True, clip_min=-2.2, clip_max=2.2,
        targeted=False
    )
    
    adv_inputs = adversary.perturb(inputs, y)
    
    with torch.no_grad():
        model.eval()
        adv_outputs = model(adv_inputs).to('cpu').numpy()
#     print(adv_outputs)
    torch.cuda.empty_cache()
    return adv_inputs.to('cpu').numpy()


def compare_with_adv(model1, model2, truth=-1):
    if truth == -1:
        truth = 1 if model1.__str__().split('-')[0] == model2.__str__().split('-')[0] else 0
    print(f'comparing:\n  model1={model1}\n  model2={model2}')
    md = ModelDiff(model1, model2)
    rand = False
    seed_inputs1 = model1.get_seed_inputs(100, rand=rand)
    seed_inputs2 = model2.get_seed_inputs(100, rand=rand)
    seed_inputs = np.concatenate([seed_inputs1, seed_inputs2])
    
    adv_inputs1 = gen_adv_inputs(model1.torch_model, seed_inputs1)
    adv_inputs2 = gen_adv_inputs(model2.torch_model, seed_inputs2)
    adv_inputs = np.concatenate([adv_inputs1, adv_inputs2])
    
#     adv_inputs_shuffle = list(adv_inputs)
#     np.random.shuffle(adv_inputs_shuffle)
#     adv_inputs_shuffle = np.array(adv_inputs_shuffle)
#     sim = md.compute_similarity_with_ddm(adv_inputs_shuffle)
#     print(f' compute_similarity_with_ddm,adv_inputs_shuffle is {sim}, truth is {truth}')

    hybrid_inputs = np.concatenate([seed_inputs1, adv_inputs1])
    
#     sim = md.compute_similarity_with_ddm(adv_inputs)
#     print(f' compute_similarity_with_ddm,adv_inputs is {sim}, truth is {truth}')
#     sim = md.compute_similarity_with_ddm(seed_inputs)
#     print(f' compute_similarity_with_ddm,seed_inputs is {sim}, truth is {truth}')
#     sim = md.compute_similarity_with_ddm(hybrid_inputs)
#     print(f' compute_similarity_with_ddm,hybrid_inputs is {sim}, truth is {truth}')
    
    sim = md.compute_similarity_with_ddv(adv_inputs)
    print(f' compute_similarity_with_ddv,adv_inputs is {sim}, truth is {truth}')
    sim = md.compute_similarity_with_ddv(seed_inputs)
    print(f' compute_similarity_with_ddv,seed_inputs is {sim}, truth is {truth}')
    sim = md.compute_similarity_with_ddv(hybrid_inputs)
    print(f' compute_similarity_with_ddv,hybrid_inputs is {sim}, truth is {truth}')
    
#     ddv_clean = md.compute_ddv(model1, seed_inputs)
#     ddv_adv = md.compute_ddv(model1, adv_inputs)
#     ddv_advshuf = md.compute_ddv(model1, adv_inputs_shuffle)
#     print(f' ddv_clean={ddv_clean}\n ddv_adv={ddv_adv}\n ddv_advshuf={ddv_advshuf}')
    
#     batch_outputs1 = model1.batch_forward(adv_inputs)
#     _, batch_preds1 = batch_outputs1.to('cpu').data.max(1)
#     batch_outputs2 = model2.batch_forward(adv_inputs)
#     _, batch_preds2 = batch_outputs2.to('cpu').data.max(1)
#     print(f'  batch_preds1={batch_preds1}\n  batch_preds2={batch_preds2}')


# compare_with_adv(models[1], models[17], 1)
test(compare_with_adv)

In [ ]:
from utils import Utils
from matplotlib import pyplot as plt

def show_images(images, labels, title='examples'):
    images = np.transpose(images, (0, 2, 3, 1))
    plt.figure(figsize=(10,10))
    plt.subplots_adjust(hspace=0.2)
    for n in range(25):
        plt.subplot(5,5,n+1)
        img = images[n]
        img = img.squeeze()
        plt.imshow(img)
        plt.title(f'{labels[n]}')
        plt.axis('off')
    _ = plt.suptitle(title)
    plt.show()

# show_images(seed_inputs, list(range(seed_inputs.shape[0])))
# print(seed_inputs[0])
# batch_outputs1 = model1.batch_forward(seed_inputs)
# batch_preds1 = batch_outputs1.to('cpu').data.max(1)
# print(batch_preds1)

In [ ]:
m = models[2]
mm = m.torch_model
test_loader = m.benchmark.get_dataloader(m.dataset_id, split='test')

# with torch.no_grad():
#     mm.eval()
#     total = 0
#     top1 = 0
#     for i, (batch, label) in enumerate(test_loader):
#         batch, label = batch.to(DEVICE), label.to(DEVICE)
#         total += batch.size(0)
#         out = mm(batch)
#         _, pred = out.max(dim=1)
#         top1 += int(pred.eq(label).sum().item())

# acc = float(top1) / total * 100
# print(top1, total, acc)

with torch.no_grad():
    for i, (images, labels) in enumerate(test_loader):
        if i != 10:
            continue
        images, labels = images.cuda(), labels.cuda()
        outputs = mm(images)
        _, preds = outputs.max(dim=1)
        print(outputs[0])
        labels = [f'{label}-{preds[i]}' for i,label in enumerate(list(labels))]
        show_images(images.to('cpu').numpy(), labels)
        break

In [ ]:
from model.fe_mobilenet import mbnetv2_dropout
import os

torch_model = mbnetv2_dropout(
            pretrained=False,
            num_classes=67
        )
ckpt = torch.load(os.path.join('models', 'train(mbnetv2,MIT67)-', 'ckpt.pth'))
torch_model.load_state_dict(ckpt['state_dict'])
mm = torch_model

In [ ]:
import torch
import torchvision
import numpy as np

from benchmark import ImageBenchmark
bench = ImageBenchmark()
models = list(bench.list_models())
for i, model in enumerate(models):
    if not model.torch_model_exists():
        continue
    if 'quantize' in model.__str__():
        continue
    acc = model.accuracy if model.dataset_id != 'ImageNet' else '-'
    print(f'{i}\t {model.__str__()} {acc}')

In [ ]:
# bench.models_dir = 'models_benchmark'
# import os
# import shutil
# import numpy as np
# from benchmark import ImageBenchmark

# bench = ImageBenchmark()
# models = list(bench.list_models())
# for i,model in enumerate(models):
#     if model.__str__().startswith('train') and 'MIT67' not in model.__str__():
#         model_path = os.path.join(model.torch_model_path, 'final_ckpt.pth')
# #         acc = model.accuracy if model.dataset_id != 'ImageNet' else '-'
# #         print(f'{i}\t {model.__str__()} {acc}')
#         new_model_dir = model.torch_model_path.replace('models', 'models_retrain')
#         new_model_path = os.path.join(new_model_dir, 'final_ckpt.pth')
#         print(new_model_path)
#         os.makedirs(new_model_dir)
#         shutil.copyfile(model_path, new_model_path)

In [44]:
l = np.array([[1, 1], [2, 2], [3, 3]])
l2 = np.array([[3, 3], [2, 2], [1, 1]])
l = torch.from_numpy(l).float()
cdist = torch.cdist(l, l, p=2.0)
cdist_mean = torch.mean(cdist)
print(cdist, cdist_mean)

reduce_dims = tuple(range(l.dim())[1:])
val = torch.mean(torch.sum((l - l2) ** 2, dim=reduce_dims) ** 0.5)
print(val)

tensor([[0.0000, 1.4142, 2.8284],
        [1.4142, 0.0000, 1.4142],
        [2.8284, 1.4142, 0.0000]]) tensor(1.2571)
tensor([2.8284, 0.0000, 2.8284], dtype=torch.float64)


In [40]:
b = torch.arange(4 * 5 * 6).view(4, 5, 6)
tuple(range(b.dim())[1:])


(1, 2)